## Imports

In [1]:
import sys

sys.path.insert(0, r"..")

import toolbox as tb

In [2]:
import importlib
import math

import numpy as np

import pandas as pd

import plotly.express as px

In [3]:
import plotly.offline
plotly.offline.init_notebook_mode()

In [4]:
importlib.reload(tb)

<module 'toolbox' from 'D:\\Code\\toolbox\\demo\\..\\toolbox\\__init__.py'>

## Modules

### tb.arraytools

#### tb.arraytools.lowpass, tb.arraytools.highpass

In [5]:
n = 20000
x = np.arange(n)
y = np.random.normal(20,5,n) + np.linspace(0, 10, n)**2

In [6]:
n_samples = 1001

y_lp = tb.arraytools.lowpass(y, n=n_samples)
y_hp = tb.arraytools.highpass(y, n=n_samples)

fig = px.line(title="lowpass and highpass demo")
fig.add_scatter(x=x, y=y, name="raw")
fig.add_scatter(x=x + n_samples / 2, y=y_lp, name="lowpass")
fig.add_scatter(x=x + n_samples / 2, y=y_hp, name="highpass")

In [7]:
# works with np.array
tb.arraytools.lowpass(np.array(y), n=n_samples)

array([ 20.04130709,  20.03908188,  20.04075977, ..., 115.05484359,
       115.06914037, 115.07585804])

In [8]:
# works with pd.Series
tb.arraytools.lowpass(pd.Series(y), n=n_samples)

500       20.041307
501       20.039082
502       20.040760
503       20.048002
504       20.037620
            ...    
19495    115.045204
19496    115.051047
19497    115.054844
19498    115.069140
19499    115.075858
Length: 19000, dtype: float64

#### tb.arraytools.interp

In [9]:
x = np.arange(100,300,10)
x

array([100, 110, 120, 130, 140, 150, 160, 170, 180, 190, 200, 210, 220,
       230, 240, 250, 260, 270, 280, 290])

In [10]:
tb.arraytools.interp(x, 2.15)

121.5

### tb.convert

In [24]:
tb.convert.radpsec_to_rpm(20)

190.9859317102744

### tb.datetimeparser

In [11]:
import datetime as dt

import toolbox.datetimeparser as dtp

In [12]:
dt_str = str(dt.datetime.now())
dt_str

'2023-05-09 14:51:09.216042'

In [13]:
dtp.ymd(dt_str)

datetime.datetime(2023, 5, 9, 14, 51, 9, 216042)

In [14]:
dtp.dmy("31.12.2023")

datetime.datetime(2023, 12, 31, 0, 0)

In [15]:
# years below 100 are automatically considered as 20XX
dtp.dmy("1.2.23 18:40:59.123456")

datetime.datetime(2023, 2, 1, 18, 40, 59, 123456)

In [16]:
dtp.dmy("1.2.23 18:40:59.123", microsecond_shift=3)

datetime.datetime(2023, 2, 1, 18, 40, 59, 123000)

In [17]:
dtp.ymd("Recording started on 2023-12-31 11:30:59.123456 in Zurich")

datetime.datetime(2023, 12, 31, 11, 30, 59, 123456)

### tb.iter

#### zip_smart

In [18]:
from toolbox.iter import zip_smart

In [19]:
# Non-strict mode:
# (default behaviour of zip, but not zip_smart)
# zip stops as soon as the shortest iterator runs out of elements.

for a, b, c, d in zip_smart(
    ("A", "B", "C", "D"),
    [1, 2, 3, 4],
    True,
    np.arange(5),
    strict=False,
):
    print(a, b, c, d)

A 1 True 0
B 2 True 1
C 3 True 2
D 4 True 3


In [20]:
# Strict mode:
# (default behaviour of zip_smart, but not zip)
# zip throws an error if the iterators do not have the same length.
# Supported in Python >= 3.10

for a, b, c, d in zip_smart(
    ("A", "B", "C", "D"),
    [1, 2, 3, 4],
    True,
    np.arange(5),
):
    print(a, b, c, d)

A 1 True 0
B 2 True 1
C 3 True 2
D 4 True 3


D:\Code\toolbox\demo\..\toolbox\iter.py:57: UserWarning:

zip's strict mode not supported in Python<3.10.

Falling back to non-strict mode.



#### sum_nested

In [21]:
from toolbox.iter import sum_nested

In [22]:
sum_nested(
    (
        1,
        [1.4, 6, 8.7, ],
        {
            "arbitrary_key": 4,
            "numpy_array": np.array((1, 2, 3.5, )),
            "pandas_Series": pd.Series((1, 2, 3.5, )),
            "further_depth": (1,2,(1,2,(1,2))),
        },
    ),
)

43.1

In [23]:
# function fails if iteration depth is exceeded
sum_nested(
    (
        1,
        [1.4, 6, 8.7, ],
        {
            "arbitrary_key": 4,
            "numpy_array": np.array((1, 2, 3.5, )),
            "pandas_Series": pd.Series((1, 2, 3.5, )),
            "further_depth": (1,2,(1,2,(1,2))),
        },
    ),
    depth=3,
)

TypeError: Iterable type detected, but recursion has reached its maximum depth.

Element:
(1, 2, (1, 2))

Type:
<class 'tuple'>

In [ ]:
sum_nested((1,1,1,(2,2,2,(3,3,3))))

In [ ]:
inp = {1:10,2:12,3:14}

# standard digestion of dicts: just use the values
print(sum_nested(inp))

# custom digestion of dicts: use the keys
print(sum_nested(
    inp,
    custom_digestion=(
        (dict, (lambda dct: [key for key, _ in dct.items()])),
    ),
))

In [ ]:
inp = ("123", "456", "789")

# parse strings as floats
print(sum_nested(
    inp,
    custom_digestion=(
        (str, (lambda s: int(s))),
    ),
))

# make checksum of strings
# hand over a list of each digit,
# which will then be handled by sum_nested.
print(sum_nested(
    inp,
    custom_digestion=(
        (str, (lambda s: [int(l) for l in s])),
    ),
))

In [ ]:
# ignore None and np.nan values
print(sum_nested(
    (
        1,
        None,
        3,
        np.nan,
        5.,
    ),
    custom_digestion=(
        (type(None), (lambda _: 0)),
        (float, (lambda x: 0 if np.isnan(x) else x)),
    ),
))

# or set custom_digestion globally
tb.iter.CUSTOM_DIGESTION = (
    (dict, (lambda dct: [elem for _, elem in dct.items()])), # still
    (type(None), (lambda _: 0)),
    (float, (lambda x: 0 if np.isnan(x) else x)),
)
print(sum_nested(
    (
        1,
        None,
        3,
        np.nan,
        5.,
    )
))